# <a href="https://thetahat.ru/courses/ad" target="_top">Введение в анализ данных</a>

В <a href="https://thetahat.ru/courses/ad/main/6/nlp_sem_part1" target="_top">предыдущем ноутбуке</a> на примере двух задач мы познакомились с новым типом нейронных сетей, а именно с RNN. Чуть ранее на занятии мы узнали, что современные LLM построены на основе архитектуры Transformer. В этом ноутбуке мы обзорно познакомимся с популярной библиотекой для работы с актуальными LLM и решим всю ту же задачу анализа тональности текста, но уже с помощью самых последних языковых моделей.

## 1. Введение в `transformers`

Что такое `transformers`? Это открытая библиотека от Hugging Face, которая предоставляет единый API для загрузки, обучения и использования различных моделей. Hugging Face через свои open-source библиотеки и платформу Hugging Face Hub предоставляет доступ к:

* Моделям. Как к коду их реализации, так и к предобученным весам, включая последние открытые LLM: Llama3, DeepSeek, Gemma3 и др.

* Пайплайнам (готовым решениям) для стандартных NLP-задач.

* Датасетам, метриками, инструментам для быстрого файнтюнинга через доп. библиотеки `datasets`, `accelerate`, `peft` и тд.


Этот ноутбук содержит базовые примеры. Более подробно с библиотекой вы сможете познакомиться на курсах DS-потока.

Что мы сделаем на семинаре:
* Посмотрим на токенизацию и чат-шаблоны (chat-template):
    * Как текст превращается в токены для современных моделей.
    * Схемы форматирования промптов для инструктивных моделей.

* Научимся генерировать текст с помощью маленьких языковых моделей:
    * Потестируем генерацию на open-source вариантах небольших современных LLM.

* Увидим, как небольшие модели (2-7B параметров) справляются с реальной задачей.
    * Классифицируем отзывы IMDB с первой части семинара.




Дополнительные материалы:
* [Документация `transformers`](https://huggingface.co/docs/transformers/index)
* [Обзорный курс от Hugging Face](https://huggingface.co/course/)
* [Примеры на Github](https://github.com/huggingface/transformers/tree/main/examples/pytorch)


In [ ]:
# установка нужных библиотек
# !pip install datasets
# !pip install vllm

In [ ]:
import torch
import transformers

from datasets import Dataset, load_dataset
from enum import Enum


from transformers import AutoModelForCausalLM, AutoTokenizer, AutoProcessor

from pprint import pprint
from pydantic import BaseModel

print(transformers.__version__)
print(torch.__version__)

4.50.0
2.6.0+cu124


Посмотрим на какую-нибудь популярную модель на [Hugging Face Hub](https://huggingface.co/models). Пользователи могут загружать свои модели для общего дсотупа.


Для работы необходимо инициализировать два объекта:

* Токенизатор. Он привязан к модели, токенизирует текст, преобразуя его в список токенов из словаря. Токенизатор используется для подготовки входных данных в нужный для модели формат.
* Модель &mdash; обычный PyTorch-модуль (torch.nn.Module) с предобученными весами. Библиотека дает возможность подключить нужный класс для задачи: классификация, генерация и т. д.

In [ ]:
# Возьмем китайскую модель qwen-2.5
# подробнее: https://github.com/QwenLM/Qwen2.5
model_name = "Qwen/Qwen2.5-3B"

# Инициализируем модель
model = AutoModelForCausalLM.from_pretrained(model_name, torch_dtype="auto", device_map="auto")

# Инициализируем токенизатор
tokenizer = AutoTokenizer.from_pretrained(model_name)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/683 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/35.6k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/2.20G [00:00<?, ?B/s]

...

generation_config.json:   0%|          | 0.00/138 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/7.23k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/2.78M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/1.67M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/7.03M [00:00<?, ?B/s]

Переведем текст в токены.

In [ ]:
# Входной текст (промпт)
inputs = "План изучения машинного обучения:\n"
# Применение токенизатора
tokenized_inputs = tokenizer(inputs, return_tensors="pt")

print("Вход модели:")
print(inputs)
print("Токенизированный вход:")
pprint(tokenized_inputs)

Вход модели:
План изучения машинного обучения:

Токенизированный вход:
{'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1]]),
 'input_ids': tensor([[ 16854, 131972,  23064,  28371,  18492, 130839,  38800, 143181,    510]])}


Попробуем предсказать следующий токен

In [ ]:
# Возьмем GPU, на котором "живет" модель
device = model.device

# Перенесем тензоры на GPU
input_ = {key: value.to(device) for key, value in tokenized_inputs.items()}

# Прогоним модель
outputs = model(**input_)

Посмотрим, какой следующий токен имеет максимальную вероятность.

In [ ]:
logits = outputs.logits  # Тензор с "сырыми" предсказаниями (логитами)
probabilities = torch.softmax(logits, dim=-1)  # Вероятности токенов
next_token_id = torch.argmax(  # Возьмем токен с макисмальной вероятностью
    probabilities[:, -1, :], dim=-1, keepdim=True
)
next_token_id

tensor([[16]], device='cuda:0')

Для того, чтобы сгенерировать осмысленное предложение, а не один токен, вызов модели необходимо обернуть в цикл. Посмотрим, как это может выглядеть.

In [ ]:
# Количество токенов, которое будем генерировать
num_tokens_to_generate = 128

for step in range(num_tokens_to_generate):
    # Прямой проход модели
    outputs = model(**input_)

    # Получаем логиты для следующего токена
    next_token_logits = outputs.logits[:, -1, :]  # [batch_size, vocab_size]
    # скрытое состояние посл-го токена ----^

    # Жадный выбор: токен с максимальной вероятностью
    next_token = torch.argmax(next_token_logits, dim=-1, keepdim=True)  # [batch_size, 1]

    # Добавляем новый токен к входным данным
    input_["input_ids"] = torch.cat([input_["input_ids"], next_token], dim=-1)

    # Обновляем маску внимания
    input_["attention_mask"] = torch.cat(
        [
            input_["attention_mask"],
            # Единичный тензор размера (1, 1) того же типа и на той же GPU
            torch.ones(
                (1, 1),
                dtype=input_["attention_mask"].dtype,
                device=input_["attention_mask"].device,
            ),
        ],
        dim=-1,
    )

    # Если достигли конца текста, останавливаемся
    if next_token == tokenizer.eos_token_id:
        break

# Декодируем результат
generated_text = tokenizer.decode(input_["input_ids"][0], skip_special_tokens=True)
print(f"Сгенерированный текст:\n\n{generated_text}")

Сгенерированный текст:

План изучения машинного обучения:
1. Основы машинного обучения
2. Структуры данных и алгоритмы машинного обучения
3. Статистика и математика для машинного обучения
4. Структуры данных и алгоритмы машинного обучения
5. Статистика и математика для машинного обучения
6. Структуры данных и алгоритмы машинного обучения
7. Статистика и математика для машинного обучения
8. Структуры данных и алгоритмы машинного обучения


В HF-моделях есть удобный метод `generate`.В нем реализованы различные стратегии генерации: жадный поиск (greedy decoding), beam search, стохастическое семплирование (с температурой, top-k, top-p) и их комбинации.

Основные параметры:

* `max_new_tokens`: максимальная длина выходной последовательности.

* `num_return_sequences`: количество вариантов текста для генерации.

* `temperature`, `top_k`, `top_p`: управляют случайностью при семплировании.

* `do_sample`: разрешает/запрещает стохастическую генерацию.

* `num_beams`: размер "пучка" (beam) для beam search.

Метод универсален для задач вроде перевода, суммаризации, ответов на вопросы или диалогов.
Подробнее о методах декодирования можно прочитать: [тут](https://huggingface.co/blog/how-to-generate)


Попробуем жадное декодирование с сравним результат с тем, что получили ранее.

In [ ]:
generated_ids = model.generate(
    **tokenized_inputs.to(model.device),
    max_new_tokens=num_tokens_to_generate,  # Максимальная длина сгенерированного текста
    do_sample=False,  # Отключаем случайность (жадный выбор)
    pad_token_id=tokenizer.eos_token_id,  # Выставим паддинг токен как токен конца генерации
)

# Декодируем обратно в текст
generated_text = tokenizer.decode(generated_ids[0], skip_special_tokens=False)
print(f"Сгенерированный текст:\n\n{generated_text}")

Сгенерированный текст:

План изучения машинного обучения:
1. Основы машинного обучения
2. Структуры данных и алгоритмы машинного обучения
3. Статистика и математика для машинного обучения
4. Структуры данных и алгоритмы машинного обучения
5. Статистика и математика для машинного обучения
6. Структуры данных и алгоритмы машинного обучения
7. Статистика и математика для машинного обучения
8. Структуры данных и алгоритмы машинного обучения


Теперь попробуем другой способ декодирования. На каждом шаге генерации у нас имеется распределение вероятностей на след. возможный токен. Мы можем попробовать сгенерировать след. токен из полученного распределения (сэмплировать).

In [ ]:
generated_ids = model.generate(
    **tokenized_inputs.to(model.device),
    max_new_tokens=num_tokens_to_generate,  # Максимальная длина текста
    do_sample=True,  # Будем использовать сэмплирование
    temperature=1.05,  # Увеличим температуру, сделаем ответы разнообразнее
    pad_token_id=tokenizer.eos_token_id,  # Чтобы избежать предупреждений
)

generated_text = tokenizer.decode(generated_ids[0], skip_special_tokens=False)
print(f"Сгенерированный текст:\n\n{generated_text}")

Сгенерированный текст:

План изучения машинного обучения:
Классификация: включает разбиение данных данных набор, где по некоторому вкладывает гипотезу
Регрессия: прогнозирование вещества, например, на основе данных набор и прогнозирования, которые будут иметь место в будущем
Анализ сообщений: подразумевает прогнозирование или извлечение данных из текстовых данных<|endoftext|>


Современные языковые модели (LLM) давно превратились в мощных диалоговых ассистентов. Такой формат взаимодействия оказался очень успешен, ведь чат-формат соответствует естественному человеческому общению, он интуитивно понятен пользователю и предоставляет собой единый интерфейс для решения разнородных задач.

Однако исходная базовая модель обучается предсказывать только следующий токен и без явных указаний может легко запутаться, т.к. возникает ряд проблем:

* Границы реплик (Где вопрос пользователя? Где ответ ассистента?)
* Что в контекста важно? Как учесть временную динамику диалога?

После базового предобучения на большом корпусе текстов обычно следует процесс инструктивного обучения на парах (запрос пользователя, ответ модели). При этом обычно модель обучают строго на определенном чат-шаблоне (chat-template), который спроектирован так, чтобы стрктурировать историю диалога в нужном формате, добавить важную информацию в контекст, указать начало и конец реплик пользователя / модели.

Пример такого шаблона:


```
<|system|> Ты ИИ-ассистент. Текущая дата: 29-03-2025. <|end_of_message|>
<|user|> Где расположен МФТИ? <|end_of_message|>
<|assistant|> Московский Физтех находится в г. Долгопрудный... <|end_of_message|>
<|user|> А сколько лет этому университету? <|end_of_message|>
<|assistant|> # Модель должна продолжить текст здесь и закончить <|end_of_message|> токеном
```

Посмотрим на `Instruct`-версию предыдущей модели.

In [ ]:
# Обратите внимание, будем использовать Instruct-версию модели!
model_name = "Qwen/Qwen2.5-3B-Instruct"

model = AutoModelForCausalLM.from_pretrained(model_name, torch_dtype="auto", device_map="auto")
tokenizer = AutoTokenizer.from_pretrained(model_name)

config.json:   0%|          | 0.00/661 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/35.6k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/2.20G [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/3.97G [00:00<?, ?B/s]

...

generation_config.json:   0%|          | 0.00/242 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/7.30k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/2.78M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/1.67M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/7.03M [00:00<?, ?B/s]

Каждая инструктивно обученная модель обычно имеет встроенный чат-шаблон (`chat-template`), тесно связанный с ее токенизатором.

Что такое чат-шаблон? Чаще всего это Jinja2-шаблон, который:
* Преобразует список сообщений в единую строку
* Добавляет служебные токены (разделители, теги ролей)
* Гарантирует совместимость формата с токенизацией модели

Каждое сообщение обычно содержит:
* `role` &mdash; роль отправителя (система, пользователь, ассистент и т.п.)
* `content` &mdash; содержимое (текст, изображения, аудио в мультимодальных моделях)

Немного обсудим типы ролей:

* `system` (или `developer`) содержит высокоуровневое описание того, как модель должна вести себя и реагировать, когда вы общаетесь с ней в чате, также там указывают другие возможные скрытые инструкции, дату, важный контекст.

* `user`'ом помечаются запросы от пользователя.

* `assistant`-реплики &mdash; это ответы, которые должна генерировать модель.

В зависимости от конкретной LLM возможны и другие роли, поэтому важно обращать внимание на рекомендованный разработчиками формат.

Рассмотрим пример.

In [ ]:
prompt = "Что такое relu в глубоком обучении?"

messages = [
    {
        "role": "system",
        "content": "You are Qwen, created by Alibaba Cloud. You are a helpful assistant.",
    },
    {"role": "user", "content": prompt},
]

Посмотрим, как выглядит шаблон.

In [ ]:
tokenizer.chat_template

'{%- if tools %}\n    {{- \'<|im_start|>system\\n\' }}\n    {%- if messages[0][\'role\'] == \'system\' %}\n        {{- messages[0][\'content\'] }}\n    {%- else %}\n        {{- \'You are Qwen, created by Alibaba Cloud. You are a helpful assistant.\' }}\n    {%- endif %}\n    {{- "\\n\\n# Tools\\n\\nYou may call one or more functions to assist with the user query.\\n\\nYou are provided with function signatures within <tools></tools> XML tags:\\n<tools>" }}\n    {%- for tool in tools %}\n        {{- "\\n" }}\n        {{- tool | tojson }}\n    {%- endfor %}\n    {{- "\\n</tools>\\n\\nFor each function call, return a json object with function name and arguments within <tool_call></tool_call> XML tags:\\n<tool_call>\\n{\\"name\\": <function-name>, \\"arguments\\": <args-json-object>}\\n</tool_call><|im_end|>\\n" }}\n{%- else %}\n    {%- if messages[0][\'role\'] == \'system\' %}\n        {{- \'<|im_start|>system\\n\' + messages[0][\'content\'] + \'<|im_end|>\\n\' }}\n    {%- else %}\n       

Применим чат-шаблон и посмотрим на результат.

In [ ]:
text = tokenizer.apply_chat_template(
    messages,
    tokenize=False,  # не будем токенизировать, а только форматируем
    add_generation_prompt=True,  # затравка для генерации
)
text

'<|im_start|>system\nYou are Qwen, created by Alibaba Cloud. You are a helpful assistant.<|im_end|>\n<|im_start|>user\nЧто такое relu в глубоком обучении?<|im_end|>\n<|im_start|>assistant\n'

Можно заметить, что `<|im_start|>` начинает реплику с указанием роли, а `<|im_end|>` служит токеном конца реплики,  отделяя текущее сообщение от следующих. В данном случае мы выставили аргумент `add_generation_prompt`, добавляющий стартовый тег ответа модели (`assistant`). Модель, продолжая текст, сгенерирует тем самым ответ ассистента.

Токенизируем обработанную строку.

In [ ]:
model_inputs = tokenizer(text, return_tensors="pt").to(model.device)
model_inputs

{'input_ids': tensor([[151644,   8948,    198,   2610,    525,   1207,  16948,     11,   3465,
            553,  54364,  14817,     13,   1446,    525,    264,  10950,  17847,
             13, 151645,    198, 151644,    872,    198,  72819,  24634, 134322,
          92874,   5805, 132853,  63469,  14746,  12228, 143180,  83098,     30,
         151645,    198, 151644,  77091,    198]], device='cuda:0'), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]], device='cuda:0')}

Сгенерируем продолжение.

In [ ]:
generated_ids = model.generate(**model_inputs, do_sample=True, max_new_tokens=1024)

Обратите внимание, `generated_ids` содержит как входные токены, так и сгенерированные.

In [ ]:
generated_ids

tensor([[151644,   8948,    198,   2610,    525,   1207,  16948,     11,   3465,
            553,  54364,  14817,     13,   1446,    525,    264,  10950,  17847,
             13, 151645,    198, 151644,    872,    198,  72819,  24634, 134322,
          92874,   5805, 132853,  63469,  14746,  12228, 143180,  83098,     30,
         151645,    198, 151644,  77091,    198,  79652,    320,   4415,   1870,
          28263,   7954,      8,   1959,  67879, 136109,  23064, 135041, 133051,
          43686,  54713,  12141, 130304,  53586,   5805,  44816,   7599,  24634,
           6020,  43686,   6709,  21032, 129568,  43686, 137528, 129250,   7587,
         130599,  63833, 126202,   6709,  21032, 129568,  43686, 137528,  21032,
             13, 134948, 126068,  42965, 137677, 130193,   1032,  23236,   1447,
             16,     13,  34348,   2247,  46705,  43758, 142567,   4235,    510,
            256,   1032,  23236, 141107, 133104,  25460,  18943,  21032,  76395,
          54713,  11916,    

Оставим только сгенерированные токены.

In [ ]:
generated_ids = [
    output_ids[len(input_ids) :]
    for input_ids, output_ids in zip(model_inputs["input_ids"], generated_ids)
]

Посмотрим на ответ модели.

In [ ]:
# batch_decode для декодирования батча, в данном случае батч размера 1
response = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)[0]
response

'ReLU (Rectified Linear Unit) — это одна из самых популярных функций активации в сверточных нейронных сетях и других типах нейронных сетей. Вот основные характеристики ReLU:\n\n1. Основная идея:\n   ReLU представляет собой линейную функцию, которая принимает вход и возвращает его без изменений, если он положительный, и 0, если он отрицательный.\n\n2. Формула:\n   \\( f(x) = \\max(0, x) \\)\n\n3. Преимущества:\n   - Простота вычислений: быстрое обучение и предсказание.\n   - Меньшая вероятность столкновения с проблемой "размытия" (vanishing gradient), особенно при глубоких слоях.\n   - Снижение размерности данных, что может ускорить обучение.\n\n4. Недостатки:\n   - Может пропускать "забытые значения" (zombie activations): значения, которые всегда будут 0, могут нести информацию о предыдущих этапах обучения.\n   - Нетограниченно градиенты: во время обратного распространения ошибки, если значение выхода становится отрицательным, градиент может быть очень большим, что может привести к "пе

Попробуем применить небольшую инструктивную LM для решения задачи с первой части семинара. Классифицируем отзывы c IMDB.

Загрузим данные.

In [ ]:
data = load_dataset("scikit-learn/imdb", split="train").train_test_split(test_size=0.2, seed=42)
data

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


DatasetDict({
    train: Dataset({
        features: ['review', 'sentiment'],
        num_rows: 40000
    })
    test: Dataset({
        features: ['review', 'sentiment'],
        num_rows: 10000
    })
})

Возьмем случайный сэмпл и посмотрим на него.

In [ ]:
random_sample = data["train"][1137]
random_sample

{'review': 'and it doesn\'t help rohmer\'s case that a few years later Syberberg came along and made a staggeringly great piece of work on the same subject (with a little help from Wagner).<br /><br />maybe this movie didn\'t look so paltry when it came out, without the syberberg film to compare it to, which was probably shot on an even smaller sound stage with fewer resources. I actually can\'t recall at the moment whether there are horses in the syberberg film. all I know is, the German version is pure magic, while this one looks like some college production documented on film for archival purposes.<br /><br />the music... la musique... isn\'t even credited here on IMDb... but someone based it on \'airs from the 12th-14th centuries" or something... well it isn\'t a great help to the film. it comes off as inauthentic and cheesy, comme le frommage mon cher!!!<br /><br />rohmer is one of those french auteurs who likes his leading men generally quite unattractive, too, and that doesn\'t 

&#x2753; **Вопрос** &#x2753;


> При использовании LLM из-за стохастичности процедуры генерации мы можем получать разные результаты для одного и того же входа. Давайте подумаем, насколько это допустимо в контексте нашей задачи классификации, и для каких задач это имеет смысл?


<details>
 <summary> Кликни для показа ответа </summary>
     > Использовать различные процедуры сэмплирования при решении задачи классификации кажется не самым разумным подходом. Это приведет к нестабильным результатам. В продакшн-системах и для получения предсказуемых результатов обычно использую жадное декодирование, что позволяет получать детерминированные предсказания. Для этого в методе `.generate` можно указать `do_sample=False`.
    Получать разнообразные ответы может быть разумно например в развлекательных чат-ботах.
</details><br/>


Сформируем запрос на классификацию в виде инструкции.

In [ ]:
messages = [{"role": "user", "content": f"Classify this sentiment: {random_sample['review']}"}]

Токенизируем лист сообщений и подготовим `Pytorch`-тензоры.

In [ ]:
def tokenize_and_apply_chat_template(messages, tokenizer):
    """Токенизация списка сообщений messages и применение чат-шаблона"""
    return tokenizer.apply_chat_template(
        messages,
        tokenize=True,
        add_generation_prompt=True,
        return_tensors="pt",
        return_dict=True,
    )


tokenized_messages = tokenize_and_apply_chat_template(messages, tokenizer).to(model.device)

tokenized_messages

{'input_ids': tensor([[151644,   8948,    198,   2610,    525,   1207,  16948,     11,   3465,
            553,  54364,  14817,     13,   1446,    525,    264,  10950,  17847,
             13, 151645,    198, 151644,    872,    198,   1957,   1437,    419,
          25975,     25,    323,    432,   3171,    944,   1492,    926,     71,
           1174,    594,   1142,    429,    264,   2421,   1635,   2937,   5718,
            652,   7725,   3697,   3156,    323,   1865,    264,  39156,  11307,
           2244,   6573,    315,    975,    389,    279,   1852,   3832,    320,
           4197,    264,   2632,   1492,    504,  51375,    568,     27,   1323,
          23976,   1323,   6206,  36760,    419,   5700,   3207,    944,   1401,
            773,  10854,   1539,    979,    432,   3697,    700,     11,   2041,
            279,   6568,    652,   7725,   4531,    311,   9429,    432,    311,
             11,    892,    572,   4658,   6552,    389,    458,   1496,   9155,
           511

Сгенерируем ответ от модели.

In [ ]:
generated_ids = model.generate(
    **tokenized_messages,
    do_sample=False,  # жадная генерация для детерменированности
    max_new_tokens=128  # макс. кол-во новых сгенерированных токенов
)

In [ ]:
input_ids_len = len(tokenized_messages["input_ids"][0])
tokenizer.decode(generated_ids[0][input_ids_len:])

'The sentiment expressed in this text is predominantly negative towards Rohmer\'s film. The reviewer criticizes several aspects of the movie:\n\n1. **Comparison to Syberberg\'s Work**: The reviewer suggests that Rohmer\'s film looks dated and inferior when compared to Syberberg\'s "staggeringly great" work, implying that Rohmer\'s film lacks the quality and depth.\n\n2. **Production Quality**: The reviewer describes the film as looking "paltry," "like some college production," and "CHEAPO! BON MARCHE!!" indicating poor production values.\n\n3. **Music**: The music is criticized as inauthentic and'

Исходя из генерации видно, что отзыв положительный, но как получить более понятный результат? Модель вроде бы выдала ответ, но возникает необходимость в его дополнительной обработке.

In [ ]:
messages = [
    {
        "role": "user",
        # Добавим пояснение, что ожидаем positive / negative ответ
        "content": f"Classify this sentiment: {random_sample['review']}. Return 'positive' or 'negative':",
    }
]

# Уже знакомый код
tokenized_messages = tokenize_and_apply_chat_template(messages, tokenizer).to(model.device)
generated_ids = model.generate(**tokenized_messages, do_sample=False, max_new_tokens=128)

input_ids_len = len(tokenized_messages["input_ids"][0])
tokenizer.decode(generated_ids[0][input_ids_len:])

'Negative<|im_end|>'

Результат получился более предсказуемый и понятный.

## 2. Введение в [`vLLM`](https://github.com/vllm-project/vllm)
Но что делать, если мы хотим например встроить языковую модель в существующие сервисы нашего проекта или компании? Библиотека `transformers` пригодна для обучения модели или инференса для прототипирования. Однако для промышленного использования она применяется редко. В рамках семинара мы очень коротко познакомимся с библиотекой `vLLM`. `vLLM` — простой в использовании фреймворк для ускоренного инференса и развертывания LLM. Библиотека содержит в себе достаточно большое количество технических особенностей и оптимизаций: Continuous Batching, PagedAttention, оптимизированные CUDA-ядра для ряда архитектур, Speculative Decoding, Structered Output и многое-многое другое. С частью из этого вы сможете познакомиться на DS-потоке!

Стоит отметить, что помимо `vLLM` есть и другие фреймворки:  `llama.cpp`, `TGI`, `sglang`, `exllamav2`, `Infinity Embeddings`, `CTranslate2`.

Загрузим модель.

*В случае использования Colab вы можете столкнуться с OOM, если попытаетесь продолжить исполнение ячеек с vLLM после загрузки HF-модели. Для простоты вам рекомендуется перезапустить среду.*

In [ ]:
from vllm import LLM, SamplingParams
from vllm.sampling_params import GuidedDecodingParams

# vLLM поддерживает модели прямо с HF
model = LLM(model="Qwen/Qwen2.5-3B-Instruct", dtype="float16")

INFO 03-28 17:34:25 [__init__.py:239] Automatically detected platform cuda.
WARNING 03-28 17:34:26 [config.py:2614] Casting torch.bfloat16 to torch.float16.
INFO 03-28 17:34:41 [config.py:585] This model supports multiple tasks: {'score', 'embed', 'classify', 'generate', 'reward'}. Defaulting to 'generate'.
WARNING 03-28 17:34:41 [arg_utils.py:1854] Compute Capability < 8.0 is not supported by the V1 Engine. Falling back to V0. 
INFO 03-28 17:34:41 [llm_engine.py:241] Initializing a V0 LLM engine (v0.8.2) with config: model='Qwen/Qwen2.5-3B-Instruct', speculative_config=None, tokenizer='Qwen/Qwen2.5-3B-Instruct', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.float16, max_seq_len=32768, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=None, enforce_eager=False, kv_cache_dtype=auto,  devi

Loading safetensors checkpoint shards:   0% Completed | 0/2 [00:00<?, ?it/s]


INFO 03-28 17:35:05 [loader.py:447] Loading weights took 20.53 seconds
INFO 03-28 17:35:06 [model_runner.py:1146] Model loading took 5.7916 GB and 21.629146 seconds
INFO 03-28 17:35:15 [worker.py:267] Memory profiling takes 8.99 seconds
INFO 03-28 17:35:15 [worker.py:267] the current vLLM instance can use total_gpu_memory (14.74GiB) x gpu_memory_utilization (0.90) = 13.27GiB
INFO 03-28 17:35:15 [worker.py:267] model weights take 5.79GiB; non_torch_memory takes 0.05GiB; PyTorch activation peak memory takes 2.52GiB; the rest of the memory reserved for KV Cache is 4.90GiB.
INFO 03-28 17:35:16 [executor_base.py:111] # cuda blocks: 8928, # CPU blocks: 7281
INFO 03-28 17:35:16 [executor_base.py:116] Maximum concurrency for 32768 tokens per request: 4.36x
INFO 03-28 17:35:20 [model_runner.py:1442] Capturing cudagraphs for decoding. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI. 

Capturing CUDA graph shapes: 100%|██████████| 35/35 [00:34<00:00,  1.00it/s]

INFO 03-28 17:35:55 [model_runner.py:1570] Graph capturing finished in 35 secs, took 0.21 GiB
INFO 03-28 17:35:55 [llm_engine.py:447] init engine (profile, create kv cache, warmup model) took 49.43 seconds


При работе с большими языковыми моделями (LLM) ключевой проблемой часто становится предсказуемость результатов. Через `vllm` мы познакомимся со структурированным выводом через контролируемую генерацию. Контролируемая генерация предполагает подход, при котором модель генерирует ответы не в произвольном формате, а строго следуя заданным шаблонам. Внутренняя техническая реализация может варьироваться, но в целом можно сказать, что сделан такой механизм через использование конечных автоматов и контролирование допустимых для генерации токенов на каждом шаге такого автомата.

Зачем это может быть полезно? Ответы в заранее заданном формате, например JSON или XML, можно сразу сохранять в базу данных или передавать другим сервисам по API. Таким образом ускоряется интеграция, исключается ручное редактирование ответов и исключаются ошибки, что делает LLM предсказуемым компонентом в вашем решении.

Зададим `GuidedDecodingParams`, который "направляет" генерацию модели, ограничивая выходные токены строго заданными значениями. В примере ниже модель обязана вернуть либо "positive", либо "negative". Другие токены невозможны.

In [ ]:
guided_decoding_params = GuidedDecodingParams(choice=["positive", "negative"])
# зададим отдельно параметры сэмплирования
sampling_params = SamplingParams(
    guided_decoding=guided_decoding_params,
    temperature=0.0,  # нулевая температура эквивалентна жадному декодированию
)

Попробуем получить ответ от модели.

In [ ]:
messages = [{"role": "user", "content": f"Classify this sentiment: {random_sample['review']}"}]
# обратите внимание, используем метод chat, а не generate!
outputs = model.chat(messages=messages, sampling_params=sampling_params)

INFO 03-28 17:37:12 [chat_utils.py:379] Detected the chat template content format to be 'string'. You can set `--chat-template-content-format` to override this.



Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]/usr/local/lib/python3.11/dist-packages/torch/utils/cpp_extension.py:2059: UserWarning: TORCH_CUDA_ARCH_LIST is not set, all archs for visible cards are included for compilation. 
If this is not desired, please set os.environ['TORCH_CUDA_ARCH_LIST'].
  warnings.warn(
Processed prompts: 100%|██████████| 1/1 [01:35<00:00, 95.27s/it, est. speed input: 4.62 toks/s, output: 0.02 toks/s]


In [ ]:
print(outputs[0].outputs[0].text)

negative


Теперь представим, что наш сервис классификации отзывов должен отдавать json в нужном формате.

In [ ]:
# Определяем структуру ответа через Pydantic
class SentimentType(str, Enum):
    positive = "positive"
    negative = "negative"


class ReviewDescription(BaseModel):
    sentiment: SentimentType  # Поле с жестко заданными вариантами


# Автоматически генерируем JSON-схему для валидации:
json_schema = ReviewDescription.model_json_schema()
json_schema

{'$defs': {'SentimentType': {'enum': ['positive', 'negative'],
   'title': 'SentimentType',
   'type': 'string'}},
 'properties': {'sentiment': {'$ref': '#/$defs/SentimentType'}},
 'required': ['sentiment'],
 'title': 'ReviewDescription',
 'type': 'object'}

Посмотрим на генерацию.

In [ ]:
guided_decoding_params = GuidedDecodingParams(json=json_schema)
sampling_params = SamplingParams(guided_decoding=guided_decoding_params, temperature=0.0)

outputs = model.chat(messages=messages, sampling_params=sampling_params)

WARNING 03-28 17:41:37 [__init__.py:33] xgrammar does not support advanced JSON schema features like enums, patterns or numeric ranges. Falling back to use outlines instead.


Processed prompts: 100%|██████████| 1/1 [00:00<00:00,  1.64it/s, est. speed input: 726.91 toks/s, output: 19.82 toks/s]


Как видим, получили валидный `json` в виде строки c нужной меткой класса.

In [ ]:
print(outputs[0].outputs[0].text)

{ "sentiment": "negative" }
